In [21]:
# !pip3 install sacrebleu

  Running setup.py bdist_wheel for sacrebleu ... done
  Stored in directory: /home/yc2462/.cache/pip/wheels/ea/0a/7d/ddcbdcd15a04b72de1b3f78e7e754aab415aff81c423376385
Successfully built sacrebleu


In [1]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random
import numpy as np

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
from sacrebleu import corpus_bleu
import os

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [2]:
words_to_load = 50000
PAD_IDX = 0
UNK_IDX = 1
SOS_IDX = 2
EOS_IDX = 3

with open('cc.zh.300.vec') as f:
    loaded_embeddings_ft = np.zeros((words_to_load+3, 300))
    words_ft = {}
    idx2words_ft = {}
    ordered_words_ft = []
    ordered_words_ft.extend(['<pad>', '<unk>', '<s>'])
    loaded_embeddings_ft[0,:] = np.zeros(300)
    loaded_embeddings_ft[1,:] = np.random.normal(size = 300)
    loaded_embeddings_ft[2,:] = np.random.normal(size = 300)
    for i, line in enumerate(f):
        if i >= words_to_load: 
            break
        s = line.split()
        loaded_embeddings_ft[i+3, :] = np.asarray(s[1:])
        words_ft[s[0]] = i+3
        idx2words_ft[i+3] = s[0]
        ordered_words_ft.append(s[0])
    words_ft['<pad>'] = PAD_IDX
    words_ft['<unk>'] = UNK_IDX
    words_ft['<s>'] = SOS_IDX
    idx2words_ft[PAD_IDX] = '<pad>'
    idx2words_ft[UNK_IDX] = '<unk>'
    idx2words_ft[SOS_IDX] = '<s>'

In [3]:
#English embedding
with open('wiki-news-300d-1M.vec') as f:
    loaded_embeddings_ft_en = np.zeros((words_to_load+4, 300))
    words_ft_en = {}
    idx2words_ft_en = {}
    ordered_words_ft_en = []
    ordered_words_ft_en.extend(['<pad>', '<unk>', '<s>', '</s>'])
    loaded_embeddings_ft_en[0,:] = np.zeros(300)
    loaded_embeddings_ft_en[1,:] = np.random.normal(size = 300)
    loaded_embeddings_ft_en[2,:] = np.random.normal(size = 300)
    loaded_embeddings_ft_en[3,:] = np.random.normal(size = 300)
    for i, line in enumerate(f):
        if i >= words_to_load: 
            break
        s = line.split()
        loaded_embeddings_ft_en[i+4, :] = np.asarray(s[1:])
        words_ft_en[s[0]] = i+4
        idx2words_ft_en[i+4] = s[0]
        ordered_words_ft_en.append(s[0])
    words_ft_en['<pad>'] = PAD_IDX
    words_ft_en['<unk>'] = UNK_IDX
    words_ft_en['<s>'] = SOS_IDX
    words_ft_en['</s>'] = EOS_IDX
    idx2words_ft_en[PAD_IDX] = '<pad>'
    idx2words_ft_en[UNK_IDX] = '<unk>'
    idx2words_ft_en[SOS_IDX] = '<s>'
    idx2words_ft_en[EOS_IDX] = '</s>'

In [4]:
#read in chinese-english pairs
lines_zh = open('iwslt-zh-en/train.tok.zh',encoding = 'utf-8').read().strip().split('\n')
lines_en = open('iwslt-zh-en/train.tok.en',encoding = 'utf-8').read().strip().split('\n')
lines_zh_test = open('iwslt-zh-en/test.tok.zh',encoding = 'utf-8').read().strip().split('\n')
lines_en_test = open('iwslt-zh-en/test.tok.en',encoding = 'utf-8').read().strip().split('\n')
lines_zh_val = open('iwslt-zh-en/dev.tok.zh',encoding = 'utf-8').read().strip().split('\n')
lines_en_val = open('iwslt-zh-en/dev.tok.en',encoding = 'utf-8').read().strip().split('\n')

In [5]:
#add sos and eos in each sentence
def add_sos_eos(lines):  
    train = []
    for l in lines:
        l = '<s> ' + l + '</s>'
        train.append(l)
    return train
zh_train = add_sos_eos(lines_zh)    
en_train = add_sos_eos(lines_en)
zh_test = add_sos_eos(lines_zh_test)
en_test = add_sos_eos(lines_en_test)
zh_val = add_sos_eos(lines_zh_val)
en_val = add_sos_eos(lines_en_val)

In [6]:
# convert token to id in the dataset
def token2index_dataset(tokens_data,eng = False):
    indices_data = []
    for tokens in tokens_data:
        index_list = []
        for token in tokens.split():
            if eng == False:
                try:
                    index_list.append(words_ft[token])
                except KeyError:
                    index_list.append(UNK_IDX)
            else:
                try:
                    index_list.append(words_ft_en[token])
                except KeyError:
                    index_list.append(UNK_IDX)
        indices_data.append(index_list)
    return indices_data

In [7]:
zh_train_indices = token2index_dataset(zh_train)
en_train_indices = token2index_dataset(en_train,eng = True)
zh_test_indices = token2index_dataset(zh_test)
en_test_indices = token2index_dataset(en_test,eng = True)
zh_val_indices = token2index_dataset(zh_val)
en_val_indices = token2index_dataset(en_val,eng = True)

In [8]:
#max_sentence_length
length_of_en = [len(x.split()) for x in en_train]
max_sentence_length_en = sorted(length_of_en)[-int(len(length_of_en)*0.01)]
length_of_zh = [len(x.split()) for x in zh_train]
max_sentence_length_zh = sorted(length_of_zh)[-int(len(length_of_zh)*0.01)]

In [9]:
sorted(length_of_zh)[-int(len(length_of_zh)*0.1)]

37

In [10]:
#Create Data Loader
import torch
from torch.utils.data import Dataset

class load_dataset(Dataset):
    """
    Class that represents a train/validation/test dataset that's readable for PyTorch
    Note that this class inherits torch.utils.data.Dataset
    """
    
    def __init__(self, data_list_s1,data_list_s2):
        """
        @param data_list_zh: list of Chinese tokens 
        @param data_list_en: list of English tokens as TARGETS
        """
        self.data_list_s1 = data_list_s1
        self.data_list_s2 = data_list_s2
        
        assert (len(self.data_list_s1) == len(self.data_list_s2))

    def __len__(self):
        return len(self.data_list_s1)
        
    def __getitem__(self, key):
        """
        Triggered when you call dataset[i]
        """
        
        token_idx_s1 = self.data_list_s1[key][:max_sentence_length_zh]
        token_idx_s2 = self.data_list_s2[key][:max_sentence_length_en]
        return [token_idx_s1, token_idx_s2, len(token_idx_s1), len(token_idx_s2)]

def collate_func(batch):
    """
    Customized function for DataLoader that dynamically pads the batch so that all 
    data have the same length
    """
    data_list_s1 = []
    data_list_s2 = []
    length_list_s1 = []
    length_list_s2 = []
    for datum in batch:
        length_list_s1.append(datum[2])
        length_list_s2.append(datum[3])
        padded_vec_zh = np.pad(np.array(datum[0]), 
                                pad_width=((0,max_sentence_length_zh-datum[2])), 
                                mode="constant", constant_values=0)
        padded_vec_en = np.pad(np.array(datum[1]), 
                                pad_width=((0,max_sentence_length_en-datum[3])), 
                                mode="constant", constant_values=0)
        data_list_s1.append(padded_vec_zh[:max_sentence_length_zh])
        data_list_s2.append(padded_vec_en[:max_sentence_length_en])
    #print(type(data_list_s1[0]))
    if torch.cuda.is_available and torch.has_cudnn:
        return [torch.from_numpy(np.array(data_list_s1)).cuda(), torch.from_numpy(np.array(data_list_s2)).cuda(),
                torch.LongTensor(length_list_s1).cuda(), torch.LongTensor(length_list_s2).cuda()]
    else:    
        return [torch.from_numpy(np.array(data_list_s1)), torch.from_numpy(np.array(data_list_s2)),
                torch.LongTensor(length_list_s1), torch.LongTensor(length_list_s2)]
    


In [11]:
BATCH_SIZE = 32
EMBEDDING_SIZE = 300 # fixed as from the input embedding data


train_dataset = load_dataset(zh_train_indices, en_train_indices)
train_loader = torch.utils.data.DataLoader(dataset=train_dataset,
                                           batch_size=BATCH_SIZE,
                                           collate_fn=collate_func,
                                           shuffle=True)

val_dataset = load_dataset(zh_val_indices, en_val_indices)
val_loader = torch.utils.data.DataLoader(dataset=val_dataset,
                                           batch_size=BATCH_SIZE,
                                           collate_fn=collate_func,
                                           shuffle=False)

### With Attention

In [12]:
class EncoderRNN(nn.Module):
    def __init__(self, emb_dim, hidden_size, embed= torch.from_numpy(loaded_embeddings_ft).float(),num_layers=1):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.emb_dim = emb_dim
        self.num_layers = num_layers 

        self.embedding = nn.Embedding.from_pretrained(embed, freeze=True)
        self.gru = nn.GRU(emb_dim, hidden_size,num_layers=num_layers,batch_first=True)

    def forward(self, data, hidden):
        
        batch_size, seq_len = data.size()
        
        embed = self.embedding(data)
        
        output, hidden = self.gru(embed,hidden)
        #hidden = [n layers * n directions =1 , batch_size, hidden_size ]
        
        return output, hidden

    # initialize the hidden with random numbers
    def initHidden(self,batch_size):
        return torch.randn(self.num_layers, batch_size, self.hidden_size,device=device)

In [13]:
class AttnDecoderRNN(nn.Module):
    def __init__(self,emb_dim,hidden_size, output_size, embed= torch.from_numpy(loaded_embeddings_ft_en).float(),num_layers=1,
                 dropout_p=0.1, max_length=max_sentence_length_zh):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers 
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding.from_pretrained(embed, freeze=True)
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)

        self.gru = nn.GRU(emb_dim, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, data, hidden,encoder_outputs):
        
        ### embed: [1 * batch size * emb_dim = 300 ] ###
        ### hidden: [1 * batch size * hidden_size = 300 ] ###
        ### encoder_outputs: [batch size * max_sentence_length_zh * hidden_size = 300 ] ###
        ### 因为这里concat之后，attn layer 他给的是 hidden size *2 
        ### 所以我这儿的hidden size就只能写300了 
        
        embed = self.embedding(data)
        embed = self.dropout(embed)    
        ### torch.cat((embed, hidden), 2)  
        ### [1 * batch size * (emb_dim + hidden_size) ]
        
        ### attn_weights: [1 * batch size * max_sentence_length_zh ]###
        ### attn_weights[0].unsqueeze(1): [batch size * 1 * max_sentence_length_zh ]###
        
        ### softmax dim=2 因为最后一个dimension是 词组什么的，不能是1，1的话就是
        ### 不同batch间这样比较了？
        attn_weights = F.softmax(
            self.attn(torch.cat((embed, hidden), 2)), dim=2)
        

        ### torch.bmm(attn_weights[0].unsqueeze(1),encoder_outputs).squeeze(1) :
        ### [batch size * 1 * hidden_size ]###

        ### attn_applied: [batch size * hidden_size (= 300) ] ###
        attn_applied = torch.bmm(attn_weights[0].unsqueeze(1), encoder_outputs).squeeze(1)
        
        ### output: [batch size * hidden_size (= 300) ] ###
        ### embed[0]: [batch size * hidden_size (= 300) ] ###

        output = torch.cat((embed[0], attn_applied), 1)
 
        ### output: [1 * batch size * hidden_size (= 300) ] ###
        output = self.attn_combine(output).unsqueeze(0)
        
        ### output: [1 * batch size * hidden_size (= 300) ] ###
        output = F.relu(output)
        
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        
        return output, hidden, attn_weights

    def initHidden(self,batch_size):
        return torch.randn(self.num_layers, batch_size, self.hidden_size,device=device)

In [14]:
teacher_forcing_ratio = 0.5
#input_tensor: list of sentence tensor
def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer,
          criterion, eee):
    
    ### target_tensor [batch size, max_sentence_length_en = 377] ###
    ### target_tensor [batch size, max_sentence_length_zh = 220] ###
    batch_size_1, input_length = input_tensor.size()
    batch_size_2, target_length = target_tensor.size()
    
    
    encoder_hidden = encoder.initHidden(batch_size_1)

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    loss = 0
    ### encoder_hidden: 1 * batch * hidden size ### 
    ### encoder_output: batch size * max_sentence_length_zh * hidden size ### 
    encoder_output, encoder_hidden = encoder(input_tensor, encoder_hidden)

    decoder_input = torch.tensor(np.array([[SOS_IDX]]*batch_size_1).reshape(1,batch_size_1),device=device)
    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False
    #print(use_teacher_forcing)
    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            
            ### decoder_output: [batchsize,5000] ###
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden,encoder_output)
            
            loss += criterion(decoder_output, target_tensor[:,di])
            decoder_input = target_tensor[:,di].unsqueeze(0)  # Teacher forcing
            
    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden,encoder_output)
                        
            ### decoder_output [batch size, 50003]  ###
            
            ### topi is a [batch size, 1] tensor first we remove the size 1
            ### demension then we add it at the beginning using squeeze
            ### 有点脑残诶，做个转置不就好了？
            
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input
            
            ### decoder_input [1, batch size]  ###
            decoder_input = decoder_input.unsqueeze(0)
 
            loss += criterion(decoder_output, target_tensor[:,di])

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

In [15]:
def trainIters(encoder, decoder, n_iters, print_every=1, plot_every=100, learning_rate=0.001):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every
    
    #--------------------------------------------	
    #	
    #    LOAD MODELS	
    #	
    #--------------------------------------------	
    folder = '.'	
    if not os.path.exists(folder):	
        os.makedirs(folder)	

    if os.path.exists('./attentation_model/Encoder_b'):	
        print('---------------------------------------------------------------------')	
        print('----------------Readind trained model---------------------------------')	
        print('---------------------------------------------------------------------')	
        	
        #read trained models	
        encoder.load_state_dict(torch.load(folder+"/Encoder_b"))
        decoder.load_state_dict(torch.load(folder+"/Decoder_b"))	
    
    encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate)
    
    criterion = nn.CrossEntropyLoss()

    for iter in range(1, n_iters + 1):
        for i, (data_s1, data_s2, lengths_s1, lengths_s2) in enumerate(train_loader):
            input_tensor = data_s1
            target_tensor = data_s2
            #print("train",target_tensor.size())
            loss = train(input_tensor, target_tensor, encoder,
                         decoder, encoder_optimizer, decoder_optimizer, criterion,i)
            print_loss_total += loss
            plot_loss_total += loss

            if i % print_every == 0:
                print_loss_avg = print_loss_total / print_every
                print_loss_total = 0
                print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                             iter, iter / n_iters * 100, print_loss_avg))

            if i % plot_every == 0:
                plot_loss_avg = plot_loss_total / plot_every
                plot_losses.append(plot_loss_avg)
                plot_loss_total = 0
                
        # Save the model for every epoch
        print('---------------------------------------------------------------------')	
        print('----------------Saving trained model---------------------------------')	
        print('---------------------------------------------------------------------')	
      
        torch.save(encoder.state_dict(),folder +"/Encoder_b")
        torch.save(decoder.state_dict(),folder +"/Decoder_b")

    
    return plot_losses



In [16]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np
%matplotlib inline

def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)
    
import time
import math

def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))


In [17]:
# beam search + bleu score
def beam_search_decoder(data, k):
    sequences = [[list(), 1.0]]
    # walk over each step in sequence
    for row in data:
        all_candidates = list()
        # expand each current candidate
        for i in range(len(sequences)):
            seq, score = sequences[i]
            for j in range(len(row)):
                candidate = [seq + [j], score * -log(row[j])]
                all_candidates.append(candidate)
        # order all candidates by score
        ordered = sorted(all_candidates, key=lambda tup:tup[1])
        # select top best
        sequences = ordered[:1]
    return sequences

In [18]:
def index2token_sentence(sentence_batch):
    return ' '.join(idx2words_ft_en[sent.item()] for sent in sentence_batch if sent.item()!=PAD_IDX)

In [19]:
import operator
#loader can be test_loader or val_loader
def evaluate(loader, encoder, decoder, beam = False, beam_k = 1):
    bleu_score_list = []
    with torch.no_grad():
        for i, (data_s1, data_s2, lengths_s1, lengths_s2) in enumerate(loader):
            print(i)
            input_tensor = data_s1
            input_length = input_tensor.size()[0]
            #sentence_length to the output length
            sentence_length = data_s2.size()[1]
            encoder_hidden = encoder.initHidden(input_length)

            encoder_output, encoder_hidden = encoder(input_tensor, encoder_hidden)
            
            #decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS
            decoder_input = torch.tensor(np.array([[SOS_IDX]]*input_length).reshape(1,input_length),device=device)

            decoder_hidden = encoder_hidden

            decoder_attentions = torch.zeros(sentence_length, sentence_length)
            decoded_words_eval = []
            sequences = [(list(), 1.0)]*beam_k
            for di in range(sentence_length):
                decoded_words_sub = []
                decoder_output, decoder_hidden, decoder_attention = decoder(
                    decoder_input, decoder_hidden, encoder_output)
                if beam == True:
                    pass
                    #initiate
                    out_sequences = []
                    if di == 0:
                        prob, elements = decoder_output.data.topk(beam_k)
                        #batch loop
                        for idx, ind in enumerate(elements):
                            sequences = []
                            for idx2 in range(beam_k):
                                seq = []
                                if ind[idx][idx2].item() == EOS_IDX
                                    seq.append('</s>')
                                else:
                                    # ind[idx][idx2] is the index of vocab
                                    seq.append(ind[idx][idx2].item())
                                sequences.append((seq, prob[idx][idx2].item()))
                            out_sequences.append(sequences)
                    else:
                        prob, elements = decoder_output.data
                        #batch loop
                        for idx, ind in enumerate(elements):
                            score_list = list(prob[idx].item())
                            updated_dic = {}
                            for idx2 in range(beam_k):
                                # vocab size list (log)prob + the (log)prob 
                                updated_score_list = score_list + [out_sequences[idx][idx2]]*len(score_list)
                                updated_score_dic = {}
                                for idx3, ele in enumerate(updated_score_list):
                                    # key is the tuple of two indices of vocab
                                    updated_score_dic[(out_sequences[idx][idx2], idx3)] = ele
                                updated_dic.update(updated_score_dic)
                            # sort all the dict values and output the keys (tuple of two indices)
                            optimal = sorted(updated_dic.items(), key=operator.itemgetter(1), reverse=True).keys[:beam_k]
                            #change a dictionary to list of tuples and override it to the out_sequences
                            out_sequences[idx] = [(v, k) for k, v in optimal.items()]
                else:
                    # topk(1) - softmax probability maximum
                    topv, topi = decoder_output.data.topk(1) 
                print(decoder_output)
                print(topi)
                #batch loop
                for ind in topi:
                    if ind.item() == EOS_IDX:
                        decoded_words_sub.append('</s>')
                        break
                    else:
                        decoded_words_sub.append(idx2words_ft_en[ind.item()])
                decoded_words_eval.append(decoded_words_sub)

                #change the dimension
                decoder_input = topi.squeeze().detach()
                decoder_input = decoder_input.unsqueeze(0)
                
            pred_num = 0
            listed_predictions = []
            #swap dimensions of decoded_words to [batch_size * 377]
            decoded_words_new = [[i for i in ele] for ele in list(zip(*decoded_words_eval))]
           # print(decoded_words_new)
            for token_list in decoded_words_new:
                sent = ' '.join(token for token in token_list if token!="<pad>")
                #print (sent)
                listed_predictions.append(sent)
                pred_num += 1
                
            ref_num = 0
            listed_reference = []
            for ele in data_s2:
                sent = index2token_sentence(ele)
                #print (tokens)
                #sent = ' '.join(tokens)
                #print (sent)
                listed_reference.append(sent)
                ref_num += 1
            
            bleu_score = corpus_bleu(listed_predictions,[listed_reference])
            print('BLEU Score is %s' % (str(bleu_score.score)))
        bleu_score_list.append(bleu_score)
        return bleu_score_list, decoded_words_new, decoder_attentions[:di + 1]

In [20]:
hidden_size = 300
encoder1 = EncoderRNN(EMBEDDING_SIZE,hidden_size).to(device)
decoder1 = AttnDecoderRNN(EMBEDDING_SIZE,hidden_size, len(ordered_words_ft)).to(device)

# ##UNCOMMENT TO TRAIN THE MODEL
# trainIters(encoder1, decoder1, 5, print_every=50)

In [21]:
output_words, attentions = evaluate(val_loader, encoder1, decoder1)

0
tensor([[-10.8925, -10.8921, -10.7258,  ..., -10.8938, -10.8001, -10.8250],
        [-10.8661, -10.8926, -10.7269,  ..., -10.8825, -10.8188, -10.8143],
        [-10.8685, -10.8826, -10.7471,  ..., -10.9097, -10.8090, -10.8190],
        ...,
        [-10.8706, -10.8651, -10.7363,  ..., -10.9274, -10.8062, -10.8094],
        [-10.8976, -10.8630, -10.7113,  ..., -10.9144, -10.8285, -10.8051],
        [-10.8626, -10.8778, -10.7081,  ..., -10.9053, -10.7933, -10.8260]],
       device='cuda:0')
tensor([[19297],
        [20295],
        [20295],
        [  176],
        [ 6188],
        [38304],
        [20295],
        [  176],
        [20295],
        [20295],
        [20295],
        [38304],
        [20295],
        [45366],
        [20295],
        [20295],
        [  176],
        [29580],
        [20295],
        [20295],
        [25269],
        [46314],
        [19297],
        [20295],
        [20295],
        [37626],
        [ 6188],
        [19297],
        [37626],
        [20

tensor([[33742],
        [33742],
        [46314],
        [33742],
        [33742],
        [33742],
        [ 1719],
        [33742],
        [46314],
        [14709],
        [33742],
        [33742],
        [33742],
        [33742],
        [46314],
        [33742],
        [14709],
        [49333],
        [33742],
        [33742],
        [14709],
        [ 1719],
        [33742],
        [33742],
        [14709],
        [49333],
        [33742],
        [46314],
        [46314],
        [33742],
        [46314],
        [33742]], device='cuda:0')
tensor([[-10.8480, -10.8223, -10.7218,  ..., -10.8566, -10.8907, -10.8427],
        [-10.8460, -10.8185, -10.7218,  ..., -10.8549, -10.8956, -10.8433],
        [-10.8533, -10.8500, -10.7254,  ..., -10.8508, -10.8691, -10.8472],
        ...,
        [-10.8496, -10.8227, -10.7228,  ..., -10.8532, -10.8967, -10.8416],
        [-10.8504, -10.8474, -10.7250,  ..., -10.8553, -10.8688, -10.8461],
        [-10.8530, -10.8253, -10.7231,  ..., 

tensor([[-10.8411, -10.8233, -10.7192,  ..., -10.8648, -10.8892, -10.8406],
        [-10.8487, -10.8234, -10.7205,  ..., -10.8539, -10.8948, -10.8439],
        [-10.8516, -10.8456, -10.7303,  ..., -10.8540, -10.8715, -10.8440],
        ...,
        [-10.8472, -10.8158, -10.7265,  ..., -10.8541, -10.8945, -10.8411],
        [-10.8481, -10.8204, -10.7225,  ..., -10.8571, -10.8891, -10.8396],
        [-10.8500, -10.8230, -10.7151,  ..., -10.8594, -10.8905, -10.8447]],
       device='cuda:0')
tensor([[33742],
        [33742],
        [46314],
        [33742],
        [33742],
        [33742],
        [46314],
        [14709],
        [33742],
        [33742],
        [14709],
        [33742],
        [33742],
        [14709],
        [ 1719],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [14709],
        [45244],
        [33742],
        [33742],
        [33742],
        [46314],
        [14709],
        [46314],
        [33742],
        [3374

tensor([[-10.8511, -10.8253, -10.7220,  ..., -10.8595, -10.8907, -10.8385],
        [-10.8448, -10.8197, -10.7179,  ..., -10.8564, -10.8952, -10.8458],
        [-10.8454, -10.8280, -10.7209,  ..., -10.8555, -10.8868, -10.8399],
        ...,
        [-10.8470, -10.8184, -10.7168,  ..., -10.8549, -10.8935, -10.8483],
        [-10.8473, -10.8174, -10.7209,  ..., -10.8572, -10.8869, -10.8400],
        [-10.8484, -10.8288, -10.7202,  ..., -10.8604, -10.8891, -10.8462]],
       device='cuda:0')
tensor([[33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [46314],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [14709],
        [ 5754],
        [33742],
        [33742],
        [14709],
        [46314],
        [33742],
        [46314],
        [33742],
        [3374

tensor([[33742],
        [33742],
        [33742],
        [33742],
        [ 7051],
        [43500],
        [46314],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [14709],
        [14709],
        [33742],
        [14709],
        [33742],
        [33742],
        [33742],
        [14709],
        [ 1838],
        [33742],
        [14709],
        [33742],
        [46314],
        [33742],
        [46314],
        [33742],
        [33742],
        [49333],
        [33742]], device='cuda:0')
tensor([[-10.8441, -10.8207, -10.7203,  ..., -10.8621, -10.8917, -10.8374],
        [-10.8526, -10.8198, -10.7185,  ..., -10.8557, -10.8932, -10.8393],
        [-10.8441, -10.8149, -10.7154,  ..., -10.8551, -10.8891, -10.8419],
        ...,
        [-10.8492, -10.8268, -10.7209,  ..., -10.8535, -10.8953, -10.8431],
        [-10.8518, -10.8381, -10.7253,  ..., -10.8653, -10.8696, -10.8438],
        [-10.8529, -10.8222, -10.7155,  ..., 

...

tensor([[-10.8552, -10.8422, -10.7250,  ..., -10.8544, -10.8800, -10.8380],
        [-10.8482, -10.8173, -10.7241,  ..., -10.8577, -10.8881, -10.8397],
        [-10.8469, -10.8200, -10.7239,  ..., -10.8557, -10.8906, -10.8414],
        ...,
        [-10.8540, -10.8290, -10.7198,  ..., -10.8577, -10.8883, -10.8478],
        [-10.8493, -10.8170, -10.7227,  ..., -10.8609, -10.8907, -10.8382],
        [-10.8456, -10.8150, -10.7280,  ..., -10.8602, -10.8889, -10.8379]],
       device='cuda:0')
tensor([[46314],
        [33742],
        [33742],
        [14709],
        [33742],
        [33742],
        [33742],
        [46314],
        [46314],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [ 7051],
        [14709],
        [33742],
        [33742],
        [33742],
        [33742],
        [46314],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [3374

tensor([[-10.8459, -10.8192, -10.7198,  ..., -10.8576, -10.8877, -10.8404],
        [-10.8473, -10.8420, -10.7247,  ..., -10.8593, -10.8719, -10.8489],
        [-10.8528, -10.8502, -10.7229,  ..., -10.8524, -10.8833, -10.8467],
        ...,
        [-10.8488, -10.8230, -10.7154,  ..., -10.8570, -10.8873, -10.8434],
        [-10.8410, -10.8174, -10.7158,  ..., -10.8556, -10.8930, -10.8431],
        [-10.8491, -10.8184, -10.7202,  ..., -10.8554, -10.8900, -10.8377]],
       device='cuda:0')
tensor([[14709],
        [33742],
        [46314],
        [33742],
        [33742],
        [34669],
        [46314],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [14709]], device='cuda:0')
tensor([[-10.8515, -10.8273, -10.7216,  ..., -10.8527, -10.8865, -10.8450],
        [-10.8450, -10.8346, -10.7236,  ..., -10.8594, -10.8823, -10.8435],
        [-10.8462, -10.8516, -10.7194,  ..., -10.8542, -10.8774, -10.8513],
        ...,
        [-10.8495, -10.818

tensor([[14709],
        [33742],
        [33742],
        [33742],
        [33742],
        [49333],
        [46314],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [14709]], device='cuda:0')
tensor([[-10.8485, -10.8292, -10.7223,  ..., -10.8559, -10.8943, -10.8440],
        [-10.8454, -10.8314, -10.7178,  ..., -10.8588, -10.8885, -10.8405],
        [-10.8475, -10.8208, -10.7229,  ..., -10.8516, -10.8907, -10.8414],
        ...,
        [-10.8476, -10.8231, -10.7203,  ..., -10.8552, -10.8916, -10.8411],
        [-10.8484, -10.8181, -10.7183,  ..., -10.8554, -10.8902, -10.8432],
        [-10.8503, -10.8260, -10.7208,  ..., -10.8548, -10.8885, -10.8468]],
       device='cuda:0')
tensor([[33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [13735],
        [34669],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742],
        [33742]], device='cuda:0')
tensor([[-10.8473, -10.8260,

BLEU Score is 0.019020797509681168


ValueError: too many values to unpack (expected 2)